Me: Josh Bevan - jbevan@bu.edu  
Get Help from RCS: help@scc.bu.edu

Our website: [rcs.bu.edu](http://rcs.bu.edu)  
Tutorial eval: [rcs.bu.edu/eval](http://rcs.bu.edu/eval)  
This notebook: http://scv.bu.edu/examples/matlab/Tutorials/PerfOpt/

# **What is "performance optimization"?**
Programs are run with finite resources: memory, cpu, disk, time, etc. For small or simple programs these limitations are unimportant; the program finishes running fast enough and within your constraints so that these limitations have no noticeable effect. However, most non-trivial programs eventually reach one of these constraints; usually memory or running time.

Performance optimization in the context of this tutorial then means improvement of a program to minimize the effect of our computing environments limitations.

You can break techniques to "PO" into several categories:
1. Memory access efficiency
2. Vectorization
3. Use of "a priori" knowledge to specialize approach/methods
4. Making use of/avoiding computer and language strengths/weaknesses
5. Algorithmic improvement: asymptotic/"big O"

Not 6: Parallelization. Improves performance, but does not "optimize" (actually usually has efficiency penalty).

In [1]:
format compact

**Brief sidebar: Recall vectorization...**
Vectorization is the process of performing the same operation on multiple pieces of data at the same time. This has to do with MATLAB's language/implementation specifics, but is also generally applicable to most other *interpreted* languages.

It often takes the form of converting "tight" loops into operations on vectors/matrices.

Here's an example:

In [2]:
nums = rand(10000,1);
%============
tic
calc = zeros(10000,1);
for t=1:1000
    for i=1:10000
        calc(i) = sin(nums(i));
    end
end
toc
%============
tic
for t=1:1000
    calc2 = sin(nums);
end
toc

Elapsed time is 0.136295 seconds.
Elapsed time is 0.081715 seconds.


Depending on MATLAB version, they may be close or not. Newer versions are able to better JIT (just-in-time) compile simple patterns. Consider this very similiar version and compare:

In [3]:
nums = rand(10000,1);
%============
tic
total = zeros(10000,1);
for t=1:1000
    for i=1:10000
        sin(nums(i));
    end
end
toc
%============
tic
for t=1:1000
    sin(nums);
end
toc

Elapsed time is 0.631402 seconds.
Elapsed time is 0.080862 seconds.


We can easily make situations where MATLAB has a hard time JITing. Try encapsulating operations inside functions:

In [ ]:
%%file test.m

function out = test(a,b)
    out = a + b;
end

In [ ]:
%%file dummy.m

function out = dummy(in)
end

In [4]:
nums = randi(100,10000,1); % Creates a 10000x1 matrix with  random integers values 1 to 100 inclusive

% Original task:
tic
for t=1:10000
    total = 0;
    for i=1:10000
        total = total + nums(i);
    end
end
toc

% Function call overhead:
tic
for t=1:10000
    total = 0;
    for i=1:10000
        total = total + nums(i);
        dummy(42)
    end
end
toc

% Original task encapsulated in function to prevent JITing:
tic
for t=1:10000
    total = 0;
    for i=1:10000
        total = test(total, nums(i));
    end
end
toc

% Optimized built-ins are even better and should be used when possible:
tic
for t=1:10000
    total = sum(nums);
end
toc

Elapsed time is 0.195207 seconds.
Elapsed time is 2.584963 seconds.
Elapsed time is 3.092294 seconds.
Elapsed time is 0.037965 seconds.


Consider a simple example that shows all of the above categories of optimization:
We want to calculate cumulative sum (prefix sum) for an array of numbers

In [5]:
nums = randi(100,10,1)

nums =
    83
    10
    21
    80
    69
    47
    90
    41
    66
    96


In [6]:
total = 0;
for i=1:numel(nums)
    total = total + nums(i);
end
total

total =
   603


In [ ]:
%%file csum.m

% Calculate a cumulative sum from a to b
% Does same amount of work as we would for a "real" csum
function total = csum(a,b)
    total = 0;
    for i=a:b
        total = total + i;
    end
end

In [ ]:
%%file csum2.m

% Calculate a cumulative sum from a to b
function total = csum2(a,b)
    total = zeros(numel(a:b),1);
    for i=a:b
        total(i) = total(i-1) + i;
    end
end

In [9]:
% Get all the cumulative sums from 1, for the numbers 1 to 100
tic
for i=1:(1*43000)
    myresults(i) = csum(1,i);
end
toc

Elapsed time is 0.983886 seconds.


In [10]:
logspace(1,5,13)

ans =
   1.0e+05 *
  Columns 1 through 7
    0.0001    0.0002    0.0005    0.0010    0.0022    0.0046    0.0100
  Columns 8 through 13
    0.0215    0.0464    0.1000    0.2154    0.4642    1.0000


In [13]:
% Look at the running time as we increase the range of numbers we get the cumsum for
c = 1;
for N=logspace(1,5,13)
    tic
    for i=1:N
        myresults(i) = csum(1,i);
    end
    timings(c) = toc;
    c = c+1;
end
plot(logspace(1,5,13),timings,'o-')
xlabel("N")
ylabel("Runtime (s)")

We can see the above plot shows our running time does not increase linearly as we increase $N$. We can talk about the "asymptotic" behavior of our program using "big O" notation. This describes the running time dependent on some critical parameter(s). In this case our critical parameter is $N$ and we'll show that our program scales as: $\mathcal{O}(N^2)$

In [12]:
% Remember "log rules":
log(2^8)
8*log(2)

ans =
    5.5452
ans =
    5.5452


In [14]:
% log-log plot of above, with linear regression in asymptotic region
loglog(logspace(1,5,13),timings,'o-')
xlabel("N")
ylabel("Runtime (s)")
polyfit(log(logspace(3,5,7)),log(timings(7:end)),1)

ans =
    1.6750  -18.0474


What can we improve?
1. Memory access efficiency
2. Vectorization
3. Use of "a priori" knowledge to specialize approach/methods
4. Making use of/avoiding computer and language strengths/weaknesses
5. Algorithmic improvement: asymptotic/"big O"

### Memory access efficiency
- preallocation versus resizing
- memory access patterns (e.g. column vs row "strides")

In [15]:
mysize=4300000;

In [29]:
clear myresults
tic
myresults(1)=1;
for i=2:mysize
    myresults(i) = myresults(i-1)+i;
    if i<10
        myresults
    end
end
toc
clear myresults

myresults =
     1     3
myresults =
     1     3     6
myresults =
     1     3     6    10
myresults =
     1     3     6    10    15
myresults =
     1     3     6    10    15    21
myresults =
     1     3     6    10    15    21    28
myresults =
     1     3     6    10    15    21    28    36
myresults =
     1     3     6    10    15    21    28    36    45
Elapsed time is 0.445246 seconds.


In [32]:
clear myresults
tic
myresults = zeros(mysize,1);
myresults(1)=1;
for i=2:mysize
    myresults(i) = myresults(i-1)+i;
    if i<10
        myresults(1:10)'
    end
end
toc
clear myresults

ans =
     1     3     0     0     0     0     0     0     0     0
ans =
     1     3     6     0     0     0     0     0     0     0
ans =
     1     3     6    10     0     0     0     0     0     0
ans =
     1     3     6    10    15     0     0     0     0     0
ans =
     1     3     6    10    15    21     0     0     0     0
ans =
     1     3     6    10    15    21    28     0     0     0
ans =
     1     3     6    10    15    21    28    36     0     0
ans =
     1     3     6    10    15    21    28    36    45     0
Elapsed time is 0.044021 seconds.


In [33]:
c = 1;
xx = logspace(1,7,13);
for N=xx
    tic
    myresults(1)=1;
    for i=2:N
        myresults(i) = myresults(i-1)+i;
    end
    timings(c) = toc;
    c = c+1;
end
loglog(xx,timings)
polyfit(log(xx(end-5:end)),log(timings(end-5:end)),1)

ans =
   0.969016065313065 -15.958886319673882


### Vectorization

In [ ]:
% If time permits...

### *a priori* knowledge

In [56]:
nums=randi(100,10,1)

nums =
    63
    10
     4
    33
    65
    59
    68
    80
    39
     8


In [57]:
% What if we want to calculate a cumulative sum every time an entry changes?
total = zeros(10,1);
total(1)=nums(1);
for i=2:numel(nums)
    total(i) = total(i-1) + nums(i);
end
before=total

before =
    63
    73
    77
   110
   175
   234
   302
   382
   421
   429


In [49]:
changed_index = randi(numel(nums))
nums(changed_index)=99

changed_index =
     5
nums =
    40
    90
    54
     9
    99
     2
    91
    38
     2
    51


In [59]:
total(1)=nums(1);
for i=2:numel(nums)
    total(i) = total(i-1) + nums(i);
end
after=total

after =
    63
    73
    77
   110
   175
   234
   302
   382
   421
   429


In [42]:
after-before

ans =
     0
     0
     0
     0
     0
     0
     0
     0
    28
    28


In [54]:
% How can we modify this to take advantage of our *a priori* knowledge?
total = zeros(10,1);
total(1)=nums(1);
for i=2:numel(nums)
    total(i) = total(i-1) + nums(i);
end
before=total
% Before change
num_changes = 100;
for i=1:num_changes
    changed_index = randi(numel(nums))
    nums(changed_index)=99;
    % After change
    total(1)=nums(1);

    total = before;
    for i=changed_index:numel(nums)
        total(i) = total(i-1) + nums(i);
    end
    after=total;
end

before =
    40
   139
   193
   202
   301
   400
   491
   590
   689
   740
changed_index =
    10
changed_index =
     9
changed_index =
     2
changed_index =
     1


Array indices must be positive integers or logical values.


### Language strengths/weaknesses

Fibonacci sequence: 1,1,2,3,5,8,13

In [ ]:
%%file myfib.m

function f = myfib(n)
    if n < 2
        f = n;
        return
    else
        f = myfib(n-1) + myfib(n-2);
    end
end

In [60]:
tic
myfib(10)
toc

ans =
    55
Elapsed time is 0.011366 seconds.


In [61]:
timer = zeros(40,1);
for i=1:40
    tic
    myfib(i);
    timer(i) = toc;
    if i>30
        i
    end
end

i =
    31
i =
    32
i =
    33
i =
    34
i =
    35
i =
    36
i =
    37
i =
    38
i =
    39
i =
    40


In [62]:
loglog(timer(10:end))

### Algorithmic improvements

*https://en.wikipedia.org/wiki/Fenwick_tree* <br>
"A flat array of N values can either store the values or the prefix sums. In the first case, computing prefix sums requires linear time; in the second case, updating the array values requires linear time (in both cases, the other operation can be performed in constant time)."

In [ ]:
nums=randi(100,10,1)

In [ ]:
N = numel(nums);
total = nums;
for i=2:N
    total(i) = total(i-1) + nums(i);
end
total

# **Advanced Vectorization Methods**

Sometimes we have two sets of data etc. that we need to interact across all elements. Imagine you have a series of partially full boxes and a variety of items you can pack in them, but you can't exceed a max weight.

In [ ]:
myboxes = [9, 11, 7, 20, 1, 19];
items = [1, 3, 4, 10, 19];
max_weight = 20;

res = zeros(numel(myboxes),numel(items));
c = 1;
for i=myboxes
    res(c,:)=(i + items);
    c=c+1;
end
res
res<=max_weight

In [ ]:
repmat(myboxes',1,numel(items))+repmat(items,numel(myboxes),1)

https://www.mathworks.com/help/matlab/ref/bsxfun.html

- Binary
- Singleton
- Expansion

In [ ]:
bsxfun(@plus,myboxes',items)

Another "advanced" technique: Use linear algebra when you can (and know how):

In [ ]:
cool

Can we write a short program using loops to find the "neighbor sum" for each element?

Is there a better way?

In [ ]:
A=toeplitz([[1 1] zeros(1,5-2)])

In [ ]:
cool
A*cool*A

# **Instrumentation/metrics**
Program bottlenecks and code performance will often defy your intuition. Therefore it's important to *empirically measure* what's going on.

Consider a simple example: based on what we've learned which of these is faster?

In [ ]:
tic
for t=1:100000
    total = 0;
    for i=1:10000
        total = total + i;
    end
end
toc

tic
for t=1:100000
    total = sum(1:10000);
end
toc

In [ ]:
total

For non-trivial programs this measurement approach is insufficient. Let's take a look at a "real" program and see how we can profile it in MATLAB.

# **Recommended algorithms starting places:**

https://en.wikipedia.org/wiki/Introduction_to_Algorithms (CLRS)

Handbook of Mathematical Functions aka Abramowitz and Stegun:

https://en.wikipedia.org/wiki/Abramowitz_and_Stegun
and
https://dlmf.nist.gov/